In [98]:
import gymnasium as gym
import numpy as np
import random
import matplotlib.pyplot as plt
from matplotlib import animation
from IPython.display import HTML

#### O Gymnasium, *aka* gym, é uma biblioteca derivada da gym do grupo OpenAI. Ela consiste em uma API que simula diversos ambientes de controle, jogos, ambientes 3D, etc... para que usuários possam aplicar técnicas de *Reinforcement Learning*

#### O objetivo desta prática é implementar uma solução de **Aprendizado por Reforço** para o *Cart Pole* que consiste em:
* Manter o pêndulo invertido orientado para cima - o ângulo do poste não deve ultrapassar o intervalo [-.2095, .2095] radianos
* O vagão deve se manter no trilho - sua posição em X deve se manter no intervalo [-2.4, 2.4]

#### Primeiramente vamos criar um ambiente do 'CartPole-v1', iniciar com o método reset() e interagir com o ambiente com alguns passos aleatórios. 

<hr>

# *Cart Pole*
* https://gymnasium.farama.org/environments/classic_control/cart_pole/

In [99]:
env = gym.make('CartPole-v1', render_mode="rgb_array")
_ = env.reset()
frames = []
actions, rewards = [], []
done = False

while not done:
    frames.append(env.render())
    action = env.action_space.sample() 
    state, reward, done, _, _ = env.step(action)
    actions.append(action)
    rewards.append(reward)

round4 = lambda x: round(x, 4)
print("Ações aleatorias:", actions, "\nRecompensa Imediata:", rewards, sep='\n')
print('\nEstado final:', 'Cart Position    |   Cart Velocity   |   Pole Angle  |   Pole Angular Velocity', sep='\n')
print(*map(round4, state), sep=" "*16)

Ações aleatorias:
[1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0]

Recompensa Imediata:
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]

Estado final:
Cart Position    |   Cart Velocity   |   Pole Angle  |   Pole Angular Velocity
0.1668                -0.1219                -0.2201                -0.3195


In [100]:
def display_frames_as_gif(frames):

    plt.ioff()
    aspect = 72
    fig, ax = plt.subplots(figsize=(frames[0].shape[1] / aspect, frames[0].shape[0] / aspect), dpi=aspect)
    patch = ax.imshow(frames[0])
    _ = plt.axis('off')

    def animate(i):
        patch.set_data(frames[i])

    anim = animation.FuncAnimation(fig, animate, frames=len(frames), interval=50, )
    return anim

anim = display_frames_as_gif(frames)
HTML(anim.to_jshtml())

# Sua implementação do *CartPole*

In [101]:
env = gym.make('CartPole-v1', render_mode = 'rgb_array')

# Q-learning parameters
alpha = 0.1  
gamma = 0.99  

epsilon_zero        =   1   #TODO # valor inicial de epsilon
epsilon_min         = 0.1   #TODO # valor final de epsilon
episodes            = 250_000   #TODO # Numero maximo de episodios do treinamento. MAXIMO PERMITIDO 250_000
min_epsilon_episode = 5000   #TODO # Episodio que o epsilon mínimo é atingido

max_steps = 500  # Número máximo de passos no treinamento. Fixo! 
epsilon = epsilon_zero
epsilon_decay = (epsilon_min-epsilon) / min_epsilon_episode  # Decaimento Linear do Epsilon, PERMITIDO ALTERAÇÕES


In [102]:
# Faça um plot da variação de epsilon durante o decorrer de 'episodes'
eps = np.maximum(np.arange(episodes)*epsilon_decay + epsilon_zero,epsilon_min)

plt.scatter(range(episodes), eps, c=eps, cmap='inferno',s=0.01)
plt.xlabel('Episodes')
plt.ylabel('Epsilon')
plt.title('Variação de Epsilon durante os Episódios')
plt.grid(True, linestyle='--', alpha=0.5)
ax = plt.gca()
ax.spines['right'].set_visible(False)
ax.spines['top'].set_visible(False)
plt.show()

In [103]:
# Define the bins for each state variable
n_bins = 10 #TODO Escolha um número de estados para cada variável
bins = [
    np.linspace(-4.8, 4.8, n_bins), #Cart Position
    np.linspace(-4, 4, n_bins), #Cart Velocity
    np.linspace(-0.418, 0.418, n_bins), #Pole Angle
    np.linspace(-4, 4, n_bins) #Pole Angular Velocity
]

def discretize_state(state, bins):
    """
    As variaveis do CartPole originalmente são contínuas. Discretize.
    Implemente a função discretize_state(state, bins) -> state_discretized
        state: list | tuple = Estado do vagão
        bins: Lista com as discretizações

        return state_discretized: tuple = Estados discretizados
        state.shape -> (4,)
    """
    state_discretized = []
    for i in range(len(state)):
        state_discretized.append(np.digitize(state[i], bins[i]) - 1)
    return tuple(state_discretized)

# Inicialização da Q-table
state_space_size = tuple([len(bins[i]) + 1 for i in range(len(bins))])
action_space_size = env.action_space.n
Q = np.zeros(state_space_size + (action_space_size,))

In [104]:
def choose_action(state, Q, epsilon):
    """
        Implemente a função choose_action(state, Q, epsilon)
        Escolha de forma probabilística conforme epsilon entre uma ação aleatória ou uma ação ótima
    """
    
    rng = np.random.uniform(0,1)
    if rng < epsilon:
        return env.action_space.sample()
    return np.argmax(Q[state])
    
def update_q_table(Q, state, action, reward, next_state, alpha, gamma):
    """
        Faça a atualização da Q-table conforme formulação do RL
    """
    error = reward + gamma*np.max(Q[next_state]) - Q[state][action]
    Q[state][action] += alpha*error

In [105]:
#Treinamento da Q-table
for episode in range(episodes):
    state, _ = env.reset()
    state = discretize_state(state, bins)
    total_reward = 0

    for step in range(max_steps):
        action = choose_action(state, Q, epsilon)
        next_state, reward, done, truncated, _ = env.step(action)
        next_state = discretize_state(next_state, bins)

        update_q_table(Q, state, action, reward, next_state, alpha, gamma)

        state = next_state
        total_reward += reward

        if done:
            break

    # Decay epsilon
    if epsilon > epsilon_min:
        epsilon = epsilon_decay*episode + epsilon_zero

    print(f"Episode {episode + 1}: Total Reward = {total_reward}")

print("Training finished.\n")

Episode 1: Total Reward = 65.0
Episode 2: Total Reward = 31.0
Episode 3: Total Reward = 26.0
Episode 4: Total Reward = 13.0
Episode 5: Total Reward = 18.0
Episode 6: Total Reward = 11.0
Episode 7: Total Reward = 15.0
Episode 8: Total Reward = 12.0
Episode 9: Total Reward = 30.0
Episode 10: Total Reward = 39.0
Episode 11: Total Reward = 16.0
Episode 12: Total Reward = 19.0
Episode 13: Total Reward = 22.0
Episode 14: Total Reward = 58.0
Episode 15: Total Reward = 15.0
Episode 16: Total Reward = 14.0
Episode 17: Total Reward = 20.0
Episode 18: Total Reward = 16.0
Episode 19: Total Reward = 12.0
Episode 20: Total Reward = 20.0
Episode 21: Total Reward = 20.0
Episode 22: Total Reward = 19.0
Episode 23: Total Reward = 10.0
Episode 24: Total Reward = 20.0
Episode 25: Total Reward = 14.0
Episode 26: Total Reward = 16.0
Episode 27: Total Reward = 15.0
Episode 28: Total Reward = 27.0
Episode 29: Total Reward = 33.0
Episode 30: Total Reward = 30.0
Episode 31: Total Reward = 25.0
Episode 32: Total

KeyboardInterrupt: 

In [ ]:
frames = []

state, _ = env.reset()
state = discretize_state(state, bins)
total_reward = 0

for step in range(max_steps):
    
    frames.append(env.render())

    action = np.argmax(Q[state])
    next_state, reward, done, truncated, _  = env.step(action)
    next_state = discretize_state(next_state, bins)

    state = next_state
    total_reward += reward
    
    if done:
        break

print(f"Test Episode {episode + 1}: Total Reward = {total_reward}")

Test Episode 10000: Total Reward = 20.0


In [ ]:
anim = display_frames_as_gif(frames)
HTML(anim.to_jshtml())

In [ ]:
# TODO implemente uma pertubação do cartpole e avalie o resultado